#### This notebook generates all the plate reader-based data figures for the paper. The order in which things happen are not necessarily in the order of the figures, but I try to explain things as I go.

In [1]:
import csv
import numpy as np
import pandas as pd
import scipy.optimize
import scipy.stats
import colorcet as cc

import statsmodels.api as sm

import bokeh.io
import bokeh.plotting
import bokeh.palettes
import bokeh.models
from bokeh.transform import jitter, factor_cmap

import tqdm
import re

import random
random.seed(42)

import iqplot
import numba
import itertools

bokeh.io.output_notebook()

import warnings
warnings.filterwarnings('ignore')

import pdb

Loading BokehJS ...

##### Functions for calibrating the plate reader fluorescence data to reduced PCA concentrations

In [2]:
def general_hill(x, Ka, n, A, B, C):
    """
    Use a generalized hill function for the calibration curve.
    """
    
    y = B + A / (C + (Ka / x) ** n)
    
    return y

def inverse_general_hill(y, Ka, n, A, B, C):
    """
    Inverse function for deriving concentrations from fluorescence values.
    """
    
    x = Ka / ((A / (y - B) - C) ** (1/n))
    
    return x

def get_calib_data(fluor_df):
    """
    Function to extract calibration data from the general dataframe(s).
    """
    
    calib_df = fluor_df.loc[fluor_df['Strain'] == 'calibration']
    calib_df['Condition Conc. (µM)'] = calib_df['Condition Conc. (µM)'].astype(float)
    
    return calib_df

def plot_calib_point(calib_df, title=None, alpha=0.05):
    """
    Plotter for the calibration data.
    """
    
    
    fig = bokeh.plotting.figure(height=400, 
                                width=600, 
                                title=title, 
                                x_axis_label='µM PCAred', 
                                y_axis_label='Fluorescence (AU)')
    
    c = fig.circle(calib_df['Condition Conc. (µM)'].values, 
                   calib_df['PCAred fluorescence (AU)'].values, 
                   size=5, 
                   alpha=alpha, 
                   legend_label='Calibration measurements')
    
    fig.legend.location = 'bottom_right'
    
    return fig
    
def fit_hill(calib_df, alpha=0.05, show_plot=False, p0=[150, 2, 40000, 5000, 1]):
    """
    Function to fit the generalized Hill function to the calibration data.
    """
    
    xdata = calib_df['Condition Conc. (µM)'].values
    ydata = calib_df['PCAred fluorescence (AU)'].values
    
    popt, pcov = scipy.optimize.curve_fit(general_hill, xdata, ydata, p0=p0)
    
    plot = plot_calib_point(calib_df, title='Fit of calibration model', alpha=alpha)
    
    x = np.linspace(0, 300, 100)
    fit = general_hill(x, *popt)
    
    plot.line(x, fit, color='black')
    
    if show_plot:
        bokeh.io.show(plot)
    
    return popt, pcov

def convert_fluor_to_conc(fluor_exp_df, popt):
    """
    Function to convert fluorescence measurements to concentrations.
    """
    
    fluor_exp_df['measured PCAred (µM)'] = [inverse_general_hill(f, *popt) for f in fluor_exp_df['PCAred fluorescence (AU)']]
    
    return fluor_exp_df

def fitting_pipeline(df, p0=[150, 2, 40000, 5000, 1], show_plot=False):
    """
    Function to bring above utilities together.
    """
    
    calib_df = get_calib_data(df)
    exp_df = df.loc[df['Strain'] != 'calibration']
    
    popt, pcov = fit_hill(calib_df, p0=p0, show_plot=show_plot)
    
    exp_df = convert_fluor_to_conc(exp_df, popt)
    
    return exp_df
    
def calibrate_by_time_point(df, p0=[150, 2, 40000, 5000, 1], show_plot=False):
    """
    Function to calibrate the data by each time point
    """
    grouped = df.groupby('Time [hr]')
    
    calibrated_dfs = []
    
    for grp in grouped:
        t = grp[0]
        mini_df = grp[1]
        
        mini_df = fitting_pipeline(mini_df, p0=p0, show_plot=show_plot)
        
        calibrated_dfs.append(mini_df)
        
    calibrated = pd.concat(calibrated_dfs)
    
    return calibrated

##### Functions for fitting the PCA oxidation curves and deriving PCA oxidation rates

In [3]:
def lowess_fit(single_data_df, timestep=5/60, window=24, plot=True):
    """
    Function to perform a LOWESS fit of PCA oxidation data.
    
    Params:
    -------
    single_data_df : pandas DataFrame
        The data for a single strain under a single condition from a single experiment.
        This is either a biological replicate from a single well or the mean of
        technical replicates from a given day.
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    window (deprecated) : int, default 24
        The number of time points oover which the LOWESS algorith should smooth.
        If the timestep is 5/60, a window of 24 corresponds to 2 hours
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    x = single_data_df['Time [hr]'].values
    y = single_data_df['measured PCAred (µM)'].values
    
    smoothed = sm.nonparametric.lowess(
        exog=x, 
        endog=y,
        is_sorted=False,
        return_sorted=True,
        frac=0.05 # scan over 5% of data
    )
    
    if plot:
        lowess_fit_plot = bokeh.plotting.figure(width=600, height=400)
        
        lowess_fit_plot.circle(x=x, y=y)
        lowess_fit_plot.line(smoothed[:,0], smoothed[:,1], line_width=2, color='red')
        
        bokeh.io.show(lowess_fit_plot)
    
    return smoothed[:,0], smoothed[:,1]

def get_lowess_derivative(lowess_x, lowess_y, timestep=5/60, plot=True):
    """
    Function to calculate the derivative of a LOWESS fit of PCA oxidation data.
    
    Params:
    -------
    lowess_x : numpy array
        The x-axis (time points) of the lowess fit
        
    lowess_y : numpy array
        The y-axis (PCAred concentration) of the lowess fit
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    derivative = np.gradient(lowess_y, timestep)
    
    if plot:
        lowess_derivative_plot = bokeh.plotting.figure(width=600, height=400)
        
        lowess_derivative_plot.line(lowess_x, derivative)
        
        bokeh.io.show(lowess_derivative_plot)
    
    return derivative

def get_max_oxidation_rate_from_lowess_fit(single_data_df, timestep=5/60, window=24, plot=True):
    """
    Function to perform a LOWESS fit of PCA oxidation data.
    
    Params:
    -------
    single_data_df : pandas DataFrame
        The data for a single strain under a single condition from a single experiment.
        This is either a biological replicate from a single well or the mean of
        technical replicates from a given day.
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    window : int, default 28
        The number of time points oover which the LOWESS algorith should smooth.
        If the timestep is 5/60, a window of 28 corresponds to 140 minutes.
        This selection is enough to smooth over some erraticity in the plate reader
        but still matches what I initially did with scanning windows with size 2
        hours
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    times = single_data_df['Time [hr]'].values
    
    interval = np.mean([x2-x1 for x2, x1 in zip(times[1:], times[:-1])])
    
    # window = 2.33 / interval
    
    lowess_x, lowess_y = lowess_fit(single_data_df, timestep=interval, window=window, plot=plot)
    
    derivative = get_lowess_derivative(lowess_x, lowess_y, timestep=interval, plot=plot)
    
    max_oxidation_rate = np.max(derivative * -1)
    
    return max_oxidation_rate

def get_time_to_thresh_from_lowess_fit(single_data_df, timestep=5/60, window=24, plot=True, thresh=0.5):
    """
    Function to perform a LOWESS fit of PCA oxidation data. Return the time
    to half maximum PCAred concentration from maximum PCAred concentration, if attained
    
    Params:
    -------
    single_data_df : pandas DataFrame
        The data for a single strain under a single condition from a single experiment.
        This is either a biological replicate from a single well or the mean of
        technical replicates from a given day.
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    window : int, default 24
        The number of time points oover which the LOWESS algorith should smooth.
        If the timestep is 5/60, a window of 24 corresponds to 2 hours
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    lowess_x, lowess_y = lowess_fit(single_data_df, timestep=timestep, window=window, plot=plot)
    
    # There are some cases with fumarate when the final [PCAred]
    # concentration is higher than the max before the oxidation
    # begins. So, I can't just take the max: I have to take the
    # maximum that comes before the minimum
    
    index_min = list(lowess_y).index(np.min(lowess_y))
    
    left_part = lowess_y[:index_min]
    if len(left_part) > 0:
        index_max = list(lowess_y).index(np.max(lowess_y[:index_min]))
    else:
        index_max = list(lowess_y).index(np.max(lowess_y))
        
    less_than_thresh = lowess_y <= np.max(lowess_y) * thresh
    try:
        index_thresh = list(less_than_thresh).index(True)
    
    except:
        return None
    
    time_to_thresh_from_max = lowess_x[index_thresh] - lowess_x[index_max]
    
    return time_to_thresh_from_max

def get_lowess_df(calibrated_df, 
                  return_param='rate', 
                  grouping=['date', 'Strain', 'Condition', 'Medium'], 
                  cat_fwd=False, 
                  thresh=0.5,
                  window=24
                 ):
    """
    Function to get a data frame for plotting max. PCA oxidation rates
    from LOWESS fitting of calibrated data.
    
    calibrated_df : pandas DataFrame
        The PCA oxidation data, calibrated by time point
    
    grouping : list, default ['date', 'Strain', 'Condition', 'Medium']
        The grouping to get unique experimental runs for data fitting
    
    cat_fwd : Bool, default True
        When True, the categories (which will be used for nested plotting by Bokeh),
        will be (Strain, Condition). When False, the categories will be (Condition, Strain)
    """
    
    
    condition_palette = bokeh.palettes.Colorblind4
    strain_palette_dict = bokeh.palettes.Category20
    
#     strains = sorted([s for s in calibrated_df['Strain'].unique() if not re.match(r'[0-9]', s[-1])])

    strains = []
    for s in calibrated_df['Strain'].unique():
        if re.match(r'[0-9]', s[-1]):
            s = s[:-1]
        
        if s not in strains:
            strains.append(s)
            
    strains = sorted(strains)
    
    strain_palette = strain_palette_dict[len(strains)]
        
    cmap = {
        'PCA': 'white',
        'PCA, DMSO': condition_palette[1],
        'PCA, NO3': condition_palette[0],
        'PCA, Fum': condition_palette[2],
        'PCA, TMAO': condition_palette[3]
    }
    
    grouped = calibrated_df.groupby(grouping)
    
    groups = []
    dates = []
    return_params = []
#     max_redox_rate_errors = []
    fill_colors = []
    line_colors = []
    shapes = []
    strain_labels = []
    
    for grp in tqdm.tqdm(grouped):
        dates.append(grp[0][0])
        condition = grp[0][2]
        
        strain = grp[0][1]
        
        if strain[-1] in [str(x) for x in range(10)]:
            # biological replicate
#             line_colors.append('black')
            shapes.append('circle')
            # strip the number so that the replicates plot together
            strain = strain[:-1]
        else:
            #technical replicate
#             line_colors.append('red')
            shapes.append('square')
            
        if cat_fwd:
            groups.append((strain, condition))
            fc = cmap[condition]
        else:
            groups.append((condition, strain))
            
            fc = strain_palette[strains.index(strain)]
            
        strain_labels.append(strain)
        
        if return_param == 'rate':
            rp = get_max_oxidation_rate_from_lowess_fit(grp[1], plot=False, window=window)
        elif return_param == 'time':
            rp = get_time_to_thresh_from_lowess_fit(grp[1], plot=False, thresh=thresh, window=window)
        
        if rp == None:
            fc = None
            lc = None
            
        else:
            lc = 'black'
            
        fill_colors.append(fc)
        line_colors.append(lc)
        return_params.append(rp)
#         max_redox_rate_errors.append(max_err)

#     error_bars = []
#     for r, e in zip (max_redox_rates, max_redox_rate_errors):
#         error_bars.append([r*-1 - e, r*-1 + e])
        
    lowess_analysis_df = pd.DataFrame({'return param': np.array(return_params), 
#                                 'err': max_redox_rate_errors, 
#                                 'err_bars': error_bars,
                                'date': dates,
                                'cat': groups,
                                'fill color': fill_colors,
                                'shape': shapes,
                                'strain': strain_labels,
                                'line color': line_colors
                           })
    
    lowess_analysis_df = lowess_analysis_df.sort_values(by=['cat', 'strain'], key=lambda x: x.str.len())
    
    return lowess_analysis_df

def lowess_plot(lowess_plot_df, 
                show=True, 
                height=600, 
                width=1200, 
                jitter_width=0.6, 
                cat_fwd=True, 
                outfile=None, 
                y_axis_label='max PCA oxidation rate (µM/hr)'
               ):
    
    lowess_bio_cds = bokeh.models.ColumnDataSource(lowess_plot_df.loc[lowess_plot_df['shape'] == 'circle'])
    lowess_tech_cds = bokeh.models.ColumnDataSource(lowess_plot_df.loc[lowess_plot_df['shape'] == 'square'])
    factors = bokeh.models.FactorRange(factors=lowess_plot_df['cat'].unique())

    TOOLTIPS = [
        ("date", "@date")
    ]

    lowess_analysis_plot = bokeh.plotting.figure(
        x_range=factors,
    #     y_axis_type='log',
        height=height,
        width=width,
        tooltips=TOOLTIPS,
        y_axis_label = y_axis_label
    )



    circle = bokeh.models.Scatter(
        y='return param', 
        x=jitter('cat', range=lowess_analysis_plot.x_range, width=jitter_width),
        fill_color='fill color', 
        line_color='line color', 
        line_width=2, 
        size=10,
        line_alpha=0.7,
        marker='circle'
    )
    
    square = bokeh.models.Scatter(
        y='return param', 
        x=jitter('cat', range=lowess_analysis_plot.x_range, width=jitter_width),
        fill_color='fill color', 
        line_color='line color', 
        line_width=2, 
        size=10,
        line_alpha=0.7,
        marker='square'
    )
    
    lowess_analysis_plot.add_glyph(lowess_bio_cds, circle)
    lowess_analysis_plot.add_glyph(lowess_tech_cds, square)
    
    bio_data = [j for j in lowess_bio_cds.data['return param'] if j]
    tech_data = [k for k in lowess_tech_cds.data['return param'] if k]
    
    if len(bio_data) == 0:
        lowess_analysis_plot.y_range.start = -0.1 * np.max(tech_data)
        
    elif len(tech_data) == 0:
        lowess_analysis_plot.y_range.start = -0.1 * np.max(bio_data)
        
    elif len(tech_data) + len(bio_data) == 0:
        lowess_analysis_plot.y_range.start = 0
        
    else:
        lowess_analysis_plot.y_range.start = np.min([-0.1 * np.max(bio_data), -0.1 * np.max(tech_data), 1.5 * np.min(bio_data), 1.5 * np.min(tech_data)])
    



    lowess_analysis_plot.xaxis.major_label_orientation = np.pi/4
    # box_plot.xaxis.group_label_orientation = np.pi/2
    lowess_analysis_plot.xaxis.major_label_text_font_size = '10pt'
    lowess_analysis_plot.yaxis.major_label_text_font_size = '10pt'
    lowess_analysis_plot.xgrid.grid_line_color = None
    lowess_analysis_plot.output_backend = 'svg'

    if show:
        bokeh.io.show(lowess_analysis_plot)
    
    if outfile:
        bokeh.io.export_svg(lowess_analysis_plot, filename=f'./plots/{outfile}_analysis_plot.svg')
        
    return lowess_analysis_plot
    

In [4]:
def get_plot_df(calibrated_df, grouping=['date', 'Strain', 'Condition', 'Medium']):
    """
    Function to pull a dataframe for a given plot out of the massive dataframe with all the data.
    """
    
    palette = bokeh.palettes.Colorblind4
    
    cmap = {
        'PCA': 'white',
        'PCA, DMSO': palette[1],
        'PCA, NO3': palette[0],
        'PCA, Fum': palette[2],
        'PCA, TMAO': palette[3]
    }
    
    grouped = calibrated_df.groupby(grouping)
    
    groups = []
    max_redox_rates = []
    max_redox_rate_errors = []
    fill_colors = []
    line_colors = []
    dates = []

    for grp in tqdm.tqdm(grouped):
    #     if grp[0][:2] not in groups:
        dates.append(grp[0][0])
        condition = grp[0][2]
        fill_colors.append(cmap[condition])
        
        strain = grp[0][1]
        if strain[-1] in [str(x) for x in range(10)]:
            # biological replicate
            line_colors.append('black')
            # strip the number so that the replicates plot together
            strain = strain[:-1]
        else:
            #technical replicate
            line_colors.append('red')
        
        
        groups.append((strain, condition))
        
        max_rate, max_err = linear_fit_scan(grp[1])
        max_redox_rates.append(max_rate)
        max_redox_rate_errors.append(max_err)

    error_bars = []
    for r, e in zip (max_redox_rates, max_redox_rate_errors):
        error_bars.append([r*-1 - e, r*-1 + e])
        
    plot_df = pd.DataFrame({'max rate': np.array(max_redox_rates)*-1, 
                                'err': max_redox_rate_errors, 
                                'err_bars': error_bars, 
                                'cat': groups,
                                'date': dates,
                                'fill color': fill_colors,
                                'line color': line_colors
                           })
    
    return plot_df

In [5]:
def get_desired_strain_data(strain_regex_list, condition_list, medium_list, calibrated_data_df):
    
    """
    Function to get data for multiple strains at once, accommodating for regular expressions
    for cases when there are biological replicates, plasmid variants, etc.
    """
    
    indexing = []
#     print(strain_regex_list)
    for s in calibrated_data_df['Strain'].values:
        
        if any([re.match(p, s) for p in strain_regex_list]):
#             print(s)
            indexing.append(True)
        else:
            indexing.append(False)
            
    strain_data = calibrated_data_df.iloc[indexing]
    
    desired_data = strain_data.loc[
    (strain_data['Condition'].isin(condition_list))
    & (strain_data['Medium'].isin(medium_list))
    & (strain_data['pregrowth condition'].isin(['shaking', 'standing', 'comparison']))
    ]
    
    return desired_data

### Load the data

In [6]:
data = pd.read_csv('./data/tidy_fluorescence_data_all_experiments.csv', index_col=0)

In [7]:
data.head()

Time [hr] Well  PCAred fluorescence (AU)       Strain   Medium Condition  \
0      0.072   A1                   38343.0  calibration  Shaking       PCA   
1      0.156   A1                   38470.0  calibration  Shaking       PCA   
2      0.239   A1                   38676.0  calibration  Shaking       PCA   
3      0.322   A1                   38689.0  calibration  Shaking       PCA   
4      0.406   A1                   38777.0  calibration  Shaking       PCA   

  Condition Conc. (µM)        date pregrowth condition  
0                  250  2021_10_19             shaking  
1                  250  2021_10_19             shaking  
2                  250  2021_10_19             shaking  
3                  250  2021_10_19             shaking  
4                  250  2021_10_19             shaking

In [8]:
# Take a look at all the different "stains"! Here you can see experiments that had to
# be tossed because of a bad TMAO batch, poor handling, etc.
data['Strain'].unique()

array(['calibration', 'Abiotic', 'WT', 'narZ-tlKO', 'narG-tlKO',
       'napA-tlKO', '∆narUZYWV', '∆narZYWV', '∆narGHJI', '∆napFDAGHBC',
       'napAnarZ-tlKO', 'narGnapA-tlKO', 'narGnarZ-tlKO',
       'napAnarZnarG-tlKO', 'double inoculum--discard',
       'preculture contamination--discard', 'PA14 1', 'PA14 2', 'PA14 3',
       'PA14 ∆napAB 1', 'PA14 ∆napAB 2', 'PA14 ∆napAB 3', 'PA14 ∆narG 1',
       'PA14 ∆narG 2', 'PA14 ∆narG 3', 'WT1', 'WT2', 'WT3', 'frdA-tlKO1',
       'frdA-tlKO2', 'frdA-tlKO3', 'frdB-tlKO1', 'frdB-tlKO2',
       'frdB-tlKO3', 'frdAB-tlKO1', 'frdAB-tlKO2', 'frdAB-tlKO3',
       'calibration_old', 'menA-tlKO', 'menAubiC-tlKO', 'blank',
       'frdA-tlKO', 'dmsA-tlKO', 'torA-tlKO', 'dmsA-tlKO1', 'dmsA-tlKO2',
       'dmsA-tlKO3', 'torA-tlKO1', 'torA-tlKO2', 'torA-tlKO3',
       'menA-tlKO1', 'menA-tlKO2', 'menA-tlKO3', 'menAubiC-tlKO1',
       'menAubiC-tlKO2', 'menAubiC-tlKO3', 'napA-tlKO1', 'napA-tlKO2',
       'napA-tlKO3', 'narZ-tlKO1', 'narZ-tlKO2', 'narZ-tlK

##### The different experiments were performed with either an old or new plate reader, and the values for fluorescence were different between them. Calibrate by date. First, check that calibration parameters are working okay for the overall curves. Then, calibrate by time point.

In [9]:
date_grouping = data.groupby('date')

for grp in date_grouping:
    date = grp[0]
    df = grp[1]
    
    calib_df = get_calib_data(df)
#     print(np.max(calib_df['Condition Conc. (µM)'].values))
    
    print(date)
    popt, pcov = fit_hill(calib_df, alpha=0.1, show_plot=True, p0=[150, 2, 40000, 5000, 1])

2021_10_19


2021_12_03


2021_12_27


2021_12_28


2022_01_07


...

2022_10_06


2022_10_07


2022_10_11


2022_11_22


2022_12_07


##### Looks like those initial parameters are good for the curve fits. Now calibrate each experiment by time point

In [10]:
date_grouping = data.groupby('date')

calibrated_dfs = []

for grp in tqdm.tqdm(date_grouping):
    date = grp[0]
    df = grp[1]
    
    calibrated_df = calibrate_by_time_point(df, p0=[150, 2, 40000, 5000, 1])
    
    calibrated_dfs.append(calibrated_df)
    
    

100%|███████████████████████████████████████████████████████████████| 19/19 [01:28<00:00,  4.68s/it]


In [11]:
calibrated_dfs[8]

Time [hr] Well  PCAred fluorescence (AU) Strain    Medium Condition  \
6924       0.068   B1                   47598.0    WT1  Standing       PCA   
7501       0.068   B2                   47148.0    WT2  Standing       PCA   
8078       0.068   B3                   47437.0    WT3  Standing       PCA   
8655       0.068   B4                   47498.0    WT1  Standing  PCA, NO3   
9232       0.068   B5                   47923.0    WT2  Standing  PCA, NO3   
...          ...  ...                       ...    ...       ...       ...   
53065     46.568   H8                    6163.0  blank  Standing       PCA   
53642     46.568   H9                    6928.0  blank  Standing       PCA   
54219     46.568  H10                    7632.0  blank  Standing       PCA   
54796     46.568  H11                    7810.0  blank  Standing       PCA   
55373     46.568  H12                    8189.0  blank  Standing       PCA   

      Condition Conc. (µM)        date pregrowth condition  \
6924                   200  2022_06_28            standing   
7501                   200  2022_06_28            standing   
8078                   200  2022_06_28            standing   
8655            200, 10000  2022_06_28            standing   
9232            200, 10000  2022_06_28            standing   
...                    ...         ...                 ...   
53065                    0  2022_06_28            standing   
53642                    0  2022_06_28            standing   
54219                    0  2022_06_28            standing   
54796                    0  2022_06_28            standing   
55373                    0  2022_06_28            standing   

       measured PCAred (µM)  
6924             198.214980  
7501             194.281223  
8078             196.799113  
8655             197.334443  
9232             201.102290  
...                     ...  
53065                   NaN  
53642                   NaN  
54219              5.279595  
54796              6.464272  
55373              8.815916  

[46956 rows x 10 columns]

##### Aggregate (take the means of) the technical replicates (biological replicates have numbers at the end to distinguish them)

In [12]:
tech_agg = calibrated_dfs[8].groupby(
    [
        'Time [hr]', 
        'Strain', 
        'Medium', 
        'Condition', 
        'Condition Conc. (µM)', 
        'pregrowth condition', 
        'date', 
#         'Well'
#         'replicate type', # Replaced this with numbers after strain ID signifying bio reps
    ]
).agg('mean').reset_index()

In [13]:
handled_replicate_types = []

for cdf in calibrated_dfs:
    
    # Biological replicates have a number after the strain ID
    # Technical replicates do not
    # Thus, can just group by strain and forget the wells
    
    # Aggregate over the strain name to catch the technical replicates
    cdf = cdf.groupby(
        [
            'Time [hr]', 
            'Strain', 
            'Medium', 
            'Condition', 
            'Condition Conc. (µM)', 
            'pregrowth condition', 
            'date', 
#             'replicate type'
        ]
    ).agg('mean').reset_index()
        
    handled_replicate_types.append(cdf)
        

In [14]:
calibrated_dfs[8].head()

Time [hr] Well  PCAred fluorescence (AU) Strain    Medium Condition  \
6924      0.068   B1                   47598.0    WT1  Standing       PCA   
7501      0.068   B2                   47148.0    WT2  Standing       PCA   
8078      0.068   B3                   47437.0    WT3  Standing       PCA   
8655      0.068   B4                   47498.0    WT1  Standing  PCA, NO3   
9232      0.068   B5                   47923.0    WT2  Standing  PCA, NO3   

     Condition Conc. (µM)        date pregrowth condition  \
6924                  200  2022_06_28            standing   
7501                  200  2022_06_28            standing   
8078                  200  2022_06_28            standing   
8655           200, 10000  2022_06_28            standing   
9232           200, 10000  2022_06_28            standing   

      measured PCAred (µM)  
6924            198.214980  
7501            194.281223  
8078            196.799113  
8655            197.334443  
9232            201.102290

In [15]:
handled_replicate_types[8]

Time [hr]      Strain    Medium  Condition Condition Conc. (µM)  \
0          0.068     Abiotic  Standing        PCA                  200   
1          0.068     Abiotic  Standing  PCA, DMSO           200, 10000   
2          0.068     Abiotic  Standing   PCA, NO3           200, 10000   
3          0.068     Abiotic  Standing  PCA, TMAO           200, 10000   
4          0.068         WT1  Standing        PCA                  200   
...          ...         ...       ...        ...                  ...   
36330     46.568  torA-tlKO2  Standing  PCA, TMAO           200, 10000   
36331     46.568  torA-tlKO3  Standing        PCA                  200   
36332     46.568  torA-tlKO3  Standing  PCA, DMSO           200, 10000   
36333     46.568  torA-tlKO3  Standing   PCA, NO3           200, 10000   
36334     46.568  torA-tlKO3  Standing  PCA, TMAO           200, 10000   

      pregrowth condition        date  PCAred fluorescence (AU)  \
0                standing  2022_06_28              48426.000000   
1                standing  2022_06_28              48806.000000   
2                standing  2022_06_28              48073.333333   
3                standing  2022_06_28              28157.333333   
4                standing  2022_06_28              47598.000000   
...                   ...         ...                       ...   
36330            standing  2022_06_28               8517.000000   
36331            standing  2022_06_28              47900.000000   
36332            standing  2022_06_28              12552.000000   
36333            standing  2022_06_28               3182.000000   
36334            standing  2022_06_28               8442.000000   

       measured PCAred (µM)  
0                205.652449  
1                209.178228  
2                202.477974  
3                 75.484572  
4                198.214980  
...                     ...  
36330             10.724195  
36331            215.330154  
36332             30.688618  
36333                   NaN  
36334             10.295984  

[36335 rows x 9 columns]

### Concatenated into one big boy

In [16]:
calibrated_data = pd.concat(handled_replicate_types)

In [17]:
calibrated_data

Time [hr]                    Strain    Medium Condition  \
0          0.072                   Abiotic   Shaking       PCA   
1          0.072                   Abiotic   Shaking  PCA, NO3   
2          0.072                        WT   Shaking       PCA   
3          0.072                        WT   Shaking  PCA, NO3   
4          0.072                 napA-tlKO   Shaking       PCA   
...          ...                       ...       ...       ...   
28268     48.068  napAnarZnarG pFE21-NarG5  Standing  PCA, NO3   
28269     48.068  napAnarZnarG pFE21-NarG6  Standing  PCA, NO3   
28270     48.068  napAnarZnarG pFE21-NarZ1  Standing  PCA, NO3   
28271     48.068  napAnarZnarG pFE21-NarZ2  Standing  PCA, NO3   
28272     48.068  napAnarZnarG pFE21-NarZ3  Standing  PCA, NO3   

      Condition Conc. (µM) pregrowth condition        date  \
0                      200             shaking  2021_10_19   
1               200, 10000             shaking  2021_10_19   
2                      200             shaking  2021_10_19   
3               200, 10000             shaking  2021_10_19   
4                      200             shaking  2021_10_19   
...                    ...                 ...         ...   
28268           200, 10000            standing  2022_12_07   
28269           200, 10000            standing  2022_12_07   
28270           200, 10000            standing  2022_12_07   
28271           200, 10000            standing  2022_12_07   
28272           200, 10000            standing  2022_12_07   

       PCAred fluorescence (AU)  measured PCAred (µM)  
0                  35779.666667            204.000219  
1                  35346.333333            197.470078  
2                  33997.333333            178.806133  
3                  33820.666667            176.745257  
4                  35629.000000            201.689624  
...                         ...                   ...  
28268              36107.000000            129.376034  
28269              35841.000000            127.813349  
28270              27806.000000             86.287697  
28271              26354.000000             79.742437  
28272              27093.000000             83.043350  

[334856 rows x 9 columns]

In [18]:
# Here you can see that I tried a bunch of different media for the assay that I don't discuss in the paper
calibrated_data['Medium'].unique()

array(['Shaking', 'PCA oxidizer basal medium', 'Shaking + POBM',
       'Standing + POBM', 'Standing + POBM + NO3', 'blank',
       'Shaking + 4-HB', 'Standing', 'Standing + NO3', 'basal medium'],
      dtype=object)

In [19]:
# This is an example oxidation curve of a random strain, in this case
# The complementation for NarZ in the triple nitrate reductase knockout background
test = calibrated_data.loc[
    (calibrated_data['Strain'].isin(['napAnarZnarG pFE21-NarZ1']))
    & (calibrated_data['Condition'].isin(['PCA, NO3']))
    & (calibrated_data['date'].isin(['2022_11_22']))
    # & (calibrated_data['Medium'].isin(['Shaking']))
]

In [20]:
test_plot = bokeh.plotting.figure(height=400, width=600)
test_plot.circle(x=test['Time [hr]'], y=test['measured PCAred (µM)'].values)
bokeh.io.show(test_plot)

In [21]:
# A general function for getting the lowess-fitted plot and dataframe
def process_to_lowess_plot(
    strain_regex_list, 
    condition_list, 
    medium_list, 
    calibrated_dataset, 
    cat_fwd=False, 
    jitter_width=0.3, 
    height=400, 
    width=1200,
    y_axis_label='max PCA oxidation rate (µM/hr)',
    outfile=None,
    return_param='rate',
    thresh=0.5,
    lowess_window=24,
    show=True
):
    
    data = get_desired_strain_data(strain_regex_list, condition_list, medium_list, calibrated_dataset)
    lowess_analysis_df = get_lowess_df(data, cat_fwd=cat_fwd, return_param=return_param, thresh=thresh, window=lowess_window)
    lowess_analysis_plot = lowess_plot(lowess_analysis_df, jitter_width=jitter_width, height=height, width=width, outfile=outfile, y_axis_label=y_axis_label, show=show)
    
    return lowess_analysis_df, lowess_analysis_plot

In [22]:
# Specific function for plotting Figure 6
def figure6_plotter(df, 
                  palette=['grey', bokeh.palettes.Colorblind4[1], bokeh.palettes.Colorblind4[3]], 
                  width=400, 
                  height=300, 
                  title='', 
                  x_axis_label='',
                  y_axis_label='',
                  show=True,
                  t_max=25
                ):
    
    fig = bokeh.plotting.figure(
        width=width,
        height=height,
        title=title,
        y_axis_label=y_axis_label,
        x_axis_label=x_axis_label
    )
    
    df = df.loc[df['Time [hr]'] <= t_max]
    
    grouped = df.groupby('Strain')
    
    color_dict = {'PA14': palette[0], 'PA14 ∆napAB': palette[1], 'PA14 ∆narG': palette[2]}
    
    for i, grp in enumerate(grouped):
        strain = grp[0]
        mini_df = grp[1]
        
        mean_df = mini_df.groupby('Time [hr]').agg('mean').reset_index()
        
        fig.circle(mini_df['Time [hr]'].values,
                   mini_df['measured PCAred (µM)'].values,
                   color=color_dict[strain],
                   alpha=0.1,
                   size=2,
                   # line_color='black',
                   )
        
        fig.line(mean_df['Time [hr]'].values,
                 mean_df['measured PCAred (µM)'].values,
                 color=color_dict[strain],
                 line_width=4,
                 line_alpha=0.5,
                 legend_label=strain
                )
        
        fig.xaxis.major_label_text_font_size = '14pt'
        fig.xaxis.axis_label_text_font_size = '14pt'
        
        fig.yaxis.major_label_text_font_size = '14pt'
        fig.yaxis.axis_label_text_font_size = '14pt'
        
        fig.title.text_font_size = '14pt'
        
        fig.output_backend = 'svg'
        
    if show:
        bokeh.io.show(fig)
        
    return fig

In [23]:

pa14_plot_df = calibrated_data.loc[(calibrated_data['Strain'].str.contains('PA14')) & (calibrated_data['Condition'] == 'PCA, NO3')]
pa14_plot_df['Strain'] = [n[:-2] for n in pa14_plot_df['Strain'].values]
pa14_plot_df.head()

Time [hr] Strain                 Medium Condition Condition Conc. (µM)  \
4      0.071   PA14         Shaking + POBM  PCA, NO3           200, 10000   
5      0.071   PA14        Standing + POBM  PCA, NO3           200, 10000   
6      0.071   PA14  Standing + POBM + NO3  PCA, NO3           200, 10000   
7      0.071   PA14         Shaking + POBM  PCA, NO3           200, 10000   
8      0.071   PA14        Standing + POBM  PCA, NO3           200, 10000   

  pregrowth condition        date  PCAred fluorescence (AU)  \
4         comparison*  2021_12_28                   38213.0   
5         comparison*  2021_12_28                   38127.0   
6         comparison*  2021_12_28                   39088.0   
7         comparison*  2021_12_28                   38261.0   
8         comparison*  2021_12_28                   38858.0   

   measured PCAred (µM)  
4            197.760575  
5            196.499813  
6            211.177808  
7            198.468588  
8            207.543201

In [24]:
pa14_pregrow_plots = []

pa14_pregrow_grouped = pa14_plot_df.groupby('Medium')

for grp in pa14_pregrow_grouped:
    med = grp[0]
    mini_df = grp[1]
    
    p = figure6_plotter(mini_df, 
                     width=400,
                     height=300,
                     x_axis_label='Time (hours)', 
                     y_axis_label='PCAred (µM)', 
                     title=med,
                     t_max=25
                    )
    
    pa14_pregrow_plots.append(p)

In [25]:
# Plots for Figure 6 ("Standing + POBM + NO3" not used in paper)
bokeh.io.export_svg(bokeh.layouts.row(pa14_pregrow_plots[:2]), filename='./plots/PA14_pregrow.svg')

['./plots/PA14_pregrow.svg']

In [26]:
# Specific plotter for Figure 3
def fig3_plotter(df, 
                  palette=bokeh.palettes.Category20[5], 
                  width=400, 
                  height=300, 
                  title='', 
                  x_axis_label='',
                  y_axis_label='',
                  show=True,
                  t_max=25
                ):
    
    fig = bokeh.plotting.figure(
        width=width,
        height=height,
        title=title,
        y_axis_label=y_axis_label,
        x_axis_label=x_axis_label
    )
    
    df = df.loc[df['Time [hr]'] <= t_max]
    
    grouped = df.groupby('Strain')
    
    for i, grp in enumerate(grouped):
        strain = grp[0]
        mini_df = grp[1]
        
        mean_df = mini_df.groupby('Time [hr]').agg('mean').reset_index()
        
        fig.circle(mini_df['Time [hr]'].values,
                   mini_df['measured PCAred (µM)'].values,
                   color=palette[i],
                   alpha=0.1,
                   size=2,
                   line_color=palette[i],
                   )
        
        fig.line(mean_df['Time [hr]'].values,
                 mean_df['measured PCAred (µM)'].values,
                 color=palette[i],
                 line_width=4,
                 line_alpha=0.5,
                 legend_label=strain
                )
        
        fig.xaxis.major_label_text_font_size = '14pt'
        fig.xaxis.axis_label_text_font_size = '14pt'
        
        fig.yaxis.major_label_text_font_size = '14pt'
        fig.yaxis.axis_label_text_font_size = '14pt'
        
        fig.title.text_font_size = '14pt'
        
        fig.output_backend = 'svg'
        
    if show:
        bokeh.io.show(fig)
        
    return fig

##### For figure 3, I want to show the technical replicates, so I need to start again from the uncalibrated/not-aggregated data and re-calibrate separately

In [27]:
figure3_df = data.loc[(data['date'] == '2021_10_19') & (data['pregrowth condition'] == 'shaking')]

In [28]:
figure3_df

Time [hr] Well  PCAred fluorescence (AU)       Strain   Medium  \
0          0.072   A1                   38343.0  calibration  Shaking   
1          0.156   A1                   38470.0  calibration  Shaking   
2          0.239   A1                   38676.0  calibration  Shaking   
3          0.322   A1                   38689.0  calibration  Shaking   
4          0.406   A1                   38777.0  calibration  Shaking   
...          ...  ...                       ...          ...      ...   
23693     23.739  G10                    3596.0  ∆napFDAGHBC  Shaking   
23694     23.822  G10                    3647.0  ∆napFDAGHBC  Shaking   
23695     23.906  G10                    3653.0  ∆napFDAGHBC  Shaking   
23696     23.989  G10                    3692.0  ∆napFDAGHBC  Shaking   
23697     24.072  G10                    3726.0  ∆napFDAGHBC  Shaking   

      Condition Condition Conc. (µM)        date pregrowth condition  
0           PCA                  250  2021_10_19             shaking  
1           PCA                  250  2021_10_19             shaking  
2           PCA                  250  2021_10_19             shaking  
3           PCA                  250  2021_10_19             shaking  
4           PCA                  250  2021_10_19             shaking  
...         ...                  ...         ...                 ...  
23693  PCA, NO3           200, 10000  2021_10_19             shaking  
23694  PCA, NO3           200, 10000  2021_10_19             shaking  
23695  PCA, NO3           200, 10000  2021_10_19             shaking  
23696  PCA, NO3           200, 10000  2021_10_19             shaking  
23697  PCA, NO3           200, 10000  2021_10_19             shaking  

[19074 rows x 9 columns]

In [29]:
figure3_df_cal = calibrate_by_time_point(figure3_df, p0=[150, 2, 40000, 5000, 1])
figure3_df_cal

Time [hr] Well  PCAred fluorescence (AU)       Strain   Medium  \
3757       0.072   B2                   35741.0      Abiotic  Shaking   
4046       0.072   B3                   34719.0           WT  Shaking   
4335       0.072   B4                   34697.0    narZ-tlKO  Shaking   
4624       0.072   B5                   35035.0    narG-tlKO  Shaking   
4913       0.072   B6                   35527.0    napA-tlKO  Shaking   
...          ...  ...                       ...          ...      ...   
22541     24.072   G6                    3028.0    napA-tlKO  Shaking   
22830     24.072   G7                   10140.0    ∆narUZYWV  Shaking   
23119     24.072   G8                    3912.0     ∆narZYWV  Shaking   
23408     24.072   G9                    3440.0     ∆narGHJI  Shaking   
23697     24.072  G10                    3726.0  ∆napFDAGHBC  Shaking   

      Condition Condition Conc. (µM)        date pregrowth condition  \
3757        PCA                  200  2021_10_19             shaking   
4046        PCA                  200  2021_10_19             shaking   
4335        PCA                  200  2021_10_19             shaking   
4624        PCA                  200  2021_10_19             shaking   
4913        PCA                  200  2021_10_19             shaking   
...         ...                  ...         ...                 ...   
22541  PCA, NO3           200, 10000  2021_10_19             shaking   
22830  PCA, NO3           200, 10000  2021_10_19             shaking   
23119  PCA, NO3           200, 10000  2021_10_19             shaking   
23408  PCA, NO3           200, 10000  2021_10_19             shaking   
23697  PCA, NO3           200, 10000  2021_10_19             shaking   

       measured PCAred (µM)  
3757             203.400220  
4046             188.402065  
4335             188.094735  
4624             192.886073  
4913             200.137799  
...                     ...  
22541                   NaN  
22830             21.487294  
23119                   NaN  
23408                   NaN  
23697                   NaN  

[15606 rows x 10 columns]

In [30]:
p1_strains = [
    'Abiotic',
    'WT',
    '∆narGHJI',
    'narG-tlKO'
]

p2_strains = [
    'Abiotic',
    'WT',
    '∆narUZYWV',
    '∆narZYWV',
    'narZ-tlKO'
]

p3_strains = [
    'Abiotic',
    'WT',
    '∆napFDAGHBC',
    'napA-tlKO'
]

In [31]:
p1_df = figure3_df_cal.loc[(figure3_df_cal['Strain'].isin(p1_strains)) & (figure3_df_cal['Condition'] == 'PCA, NO3')]
p2_df = figure3_df_cal.loc[(figure3_df_cal['Strain'].isin(p2_strains)) & (figure3_df_cal['Condition'] == 'PCA, NO3')]
p3_df = figure3_df_cal.loc[(figure3_df_cal['Strain'].isin(p3_strains)) & (figure3_df_cal['Condition'] == 'PCA, NO3')]

In [32]:
fig3_palette = [
    'grey',
    bokeh.palettes.Colorblind4[0], 
    bokeh.palettes.Colorblind4[1],
    bokeh.palettes.Colorblind4[3],
    bokeh.palettes.Colorblind4[2], 
]

In [33]:
narG = fig3_plotter(p1_df, 
                     width=400, 
                     x_axis_label='Time (hours)', 
                     y_axis_label='PCAred (µM)', 
                     title='NarG comparison',
                     palette=fig3_palette,
                     t_max=10
                    )

In [34]:
narZ = fig3_plotter(p2_df, 
                     width=400, 
                     x_axis_label='Time (hours)', 
                     y_axis_label='PCAred (µM)', 
                     title='NarZ comparison',
                     palette=fig3_palette
                    )

In [35]:
napA = fig3_plotter(p3_df, 
                     width=400, 
                     x_axis_label='Time (hours)', 
                     y_axis_label='PCAred (µM)', 
                     title='NapA comparison',
                     palette=fig3_palette,
                     t_max=10
                    )

In [36]:
# Plots for Figure 3
bokeh.io.export_svg(bokeh.layouts.row([narZ, narG, napA]), filename='./plots/datsenkowanner_recombineering_comparison.svg')

['./plots/datsenkowanner_recombineering_comparison.svg']

### Functions for bootstrapped hypothesis testing

#### Borrowing functions and strategy from Jusin Bois (https://bebi103a.github.io/lessons/17/hacker_nhst.html?highlight=bootstrap) and applying the algorithm described by Efron and Tibshirani from Efron B, Tibshirani R. An introduction to the bootstrap. Nachdr. Boca Raton, Fla.: Chapman & Hall; 1998. 436 p. (Monographs on statistics and applied probability) (Algorithm 16.2).

In [37]:
def shift_means(x, y):
    """Shift distributions to have the same mean (null hypothesis
    is that means are equal)"""
    
    total_mean = np.mean(np.concatenate((x, y)))
    x_shift = x - np.mean(x) + total_mean
    y_shift = y - np.mean(y) + total_mean
    
    return x_shift, y_shift

@numba.njit
def draw_bs_sample(data):
    """Draw a bootstrap sample from a 1D data set."""
    return np.random.choice(data, size=len(data))

@numba.njit
def draw_bs_reps_diff_mean(x, y, size=1):
    """
    Generate bootstrap replicates with difference of means
    as the test statistic.
    """
    out = np.empty(size)
    for i in range(size):
        out[i] = np.mean(draw_bs_sample(x)) - np.mean(draw_bs_sample(y))

    return out

def bootstrap_hypothesis_test_mean(set1, set2, num_permutations=1000000):
    
    # pdb.set_trace()
    if (np.isnan(set1)).all() or (np.isnan(set2)).all():
        return None
    set1 = set1[~np.isnan(set1)]
    set2 = set2[~np.isnan(set2)]
    
    if (len(set1) < 3) or (len(set2) < 3):
        return None
    
    diff_mean = np.mean(set1) - np.mean(set2)
    
    shift_set1, shift_set2 = shift_means(set1, set2)
    
    bs_reps = draw_bs_reps_diff_mean(shift_set1, shift_set2, size=num_permutations)
    p_val = np.sum(np.abs(bs_reps) >= np.abs(diff_mean)) / len(bs_reps)
    return p_val


@numba.jit
def t_stat(set1, set2, size=1):
    
    out = np.empty(size)
    for i in range(size):
        t = ( np.mean(draw_bs_sample(set1)) - np.mean(draw_bs_sample(set2)) ) / np.sqrt( np.var(set1)/len(set1) + np.var(set2)/len(set2) )
        out[i] = np.abs(t)

    return out

    
def bootstrap_efron_tibshirani(set1, set2, num_permutations=1000000):
    """
    
    Efron B, Tibshirani R. An introduction to the bootstrap. Nachdr. Boca Raton, Fla.: Chapman & Hall; 1998. 
    436 p. (Monographs on statistics and applied probability). 

    
    https://en.wikipedia.org/wiki/Bootstrapping_(statistics)#Bootstrap_hypothesis_testing
    """
    
    if (np.isnan(set1)).all() or (np.isnan(set2)).all():
        return None
    set1 = set1[~np.isnan(set1)]
    set2 = set2[~np.isnan(set2)]
    
    if (len(set1) < 3) or (len(set2) < 3):
        return None
    
    t = ( np.mean(set1) - np.mean(set2) ) / np.sqrt( np.var(set1)/len(set1) + np.var(set2)/len(set2) )
    # print(t)
    
    shift_set1, shift_set2 = shift_means(set1, set2)
    # print(shift_set1)
    # print(shift_set2)
    
    t_boots = t_stat(shift_set1, shift_set2, size=num_permutations)
    # print(t_boots)
    
    p_val = np.sum(np.abs(t_boots) >= np.abs(t)) / len(t_boots)
    
    return p_val
    
    

In [38]:
def get_pval_df(lowess_analysis_df, func=bootstrap_efron_tibshirani, num_permutations=1000000):
    """
    Function to do pairwise comparisons of all strains for a given experiment
    """
    
    x = []
    y = []
    p_vals = []
    labels = []
    colors = []
    legends = []
    
    strains = lowess_analysis_df['strain'].unique()
    
    pairs = []
    for s1 in strains:
        for s2 in strains:
            if ((s2, s1) not in pairs) and (s1 != s2):
                pairs.append((s1, s2))
    
    # bonferroni_threshold = 0.05/len(pairs)

    for s1, s2 in tqdm.tqdm(pairs):
        # print(s1, s2)       
        set1 = lowess_analysis_df.loc[lowess_analysis_df['strain'] == s1]['return param'].values.astype(float)
        set2 = lowess_analysis_df.loc[lowess_analysis_df['strain'] == s2]['return param'].values.astype(float)
        # pdb.set_trace()
        p_val = func(set1, set2, num_permutations=num_permutations)
        
        x.append(s1)
        y.append(s2)
        p_vals.append(p_val)


    pval_df = pd.DataFrame.from_dict({'x': x, 
                                      'y': y, 
                                      'p_val': p_vals, 
                                     })
    
    pval_df = pval_df.dropna()
    
    bonferroni_threshold = 0.05/len(pval_df)
    
    for p in pval_df['p_val'].values:
        
        if p < bonferroni_threshold:
            color = bokeh.palettes.Colorblind4[3]
            legend = f'**p < {bonferroni_threshold:.2e}'
            label = '**'
            
        elif p < 0.05:
            color = bokeh.palettes.Colorblind4[1]
            legend = f'*{bonferroni_threshold:.2e} ≤ p < 0.05'
            label = '*'    
            
        elif p >= 0.05:
            color = ' gainsboro'
            legend = 'p ≥ 0.05'
            label = ''
            
        labels.append(label)
        colors.append(color)
        legends.append(legend)
        
    pval_df['label'] = labels
    pval_df['color'] = colors
    pval_df['legend'] = legends
        
    
    return pval_df

In [39]:
def plot_pval_heatmap(pval_df, outfile=None, show=True, width=400, height=400):
    
    """
    Function to generate the heatmap corresponding to all the pairwise comparisons
    """
    
    
    from bokeh.transform import linear_cmap, log_cmap, factor_cmap
    from bokeh.models import (BasicTicker, LogTicker, ColorBar, ColumnDataSource,
                              LinearColorMapper, LogColorMapper, PrintfTickFormatter, LabelSet)

    
    TOOLS = "pan,wheel_zoom,box_zoom,reset,hover,save"

    TOOLTIPS = [
        ("(x, y)", "(@x, @y)"),
        ("fill color", "@color"),
        ("p_val", "@p_val"),
        ("label", "@label"),
    ]

    source = ColumnDataSource(pval_df)
    pval_heat = bokeh.plotting.figure(
        x_range=pval_df['y'].unique(),
        y_range=list(reversed(pval_df['x'].unique())),
        width=width,
        height=height,
        tools=TOOLS,
        tooltips=TOOLTIPS,
    )


    r = pval_heat.rect(x='y', y='x', width=1, height=1, source=pval_df,
                       fill_color='color',
                       line_color='black',
                       legend_group='legend'
                      )

    t = pval_heat.text(x='y', 
                       y='x', 
                       source=pval_df, 
                       text='label', 
                       text_align='center', 
                       text_color='white',
                       text_font_size='16pt',
                       y_offset=17,
                       text_font_style='bold',
                       # text_font={'value': 'arial'}
                       # text_outline_color='black'
                      )

    # labelset = LabelSet(x='y', 
    #                     y='x', 
    #                     text='label', 
    #                     y_offset=-4, 
    #                     source=source,
    #                     text_align='center',
    #                     text_color='black',
    #                     text_font_size='9pt',
    #                     background_fill_color='grey'
    #                    )

    pval_heat.xaxis.major_label_orientation = np.math.pi/4
    pval_heat.grid.grid_line_color = None
    pval_heat.xaxis.major_label_text_font_size = '10pt'
    pval_heat.yaxis.major_label_text_font_size = '10pt'


    pval_heat.legend.location = 'bottom_left'
    
    pval_heat.legend.border_line_color = None
    pval_heat.legend.border_line_alpha = 0
    pval_heat.legend.background_fill_alpha = 0
    pval_heat.legend.margin = 3
    pval_heat.legend.spacing = 3
    
    pval_heat.output_backend = 'svg'

    if show:
        bokeh.io.show(pval_heat)
    
    if outfile:
        bokeh.io.export_svg(pval_heat, filename=f'./plots/{outfile}_pval_heat.svg')
    
    return pval_heat

In [40]:
def bootstrapping(
    strain_regex_list, 
    condition_list, 
    medium_list, 
    calibrated_dataset,
    func=bootstrap_efron_tibshirani, # The median test gives bogus results on small datasets with high variance
    cat_fwd=False, 
    jitter_width=0.3, 
    height=400, 
    width1=400,
    width2=400,
    y_axis_label='max PCA oxidation rate (µM/hr)',
    outfile=None,
    return_param='rate',
    thresh=0.5,
    lowess_window=24,
    show=True
):
    
    """
    Function to run the bootstrapped hypothesis tests on a given experiment.
    """
    
    data = get_desired_strain_data(
        strain_regex_list, 
        condition_list, 
        medium_list, 
        calibrated_dataset
    )
    
    lowess_analysis_df, rate_plot = process_to_lowess_plot(strain_regex_list, 
                                      condition_list, 
                                      medium_list, 
                                      calibrated_dataset, 
                                      width=width1,
                                      height=height,
                                      outfile=outfile,
                                      return_param=return_param,
                                      y_axis_label=y_axis_label,
                                      show=show
                                     )
    

    pval_df = get_pval_df(lowess_analysis_df, func=func)
    
    pval_heat = plot_pval_heatmap(pval_df, outfile=outfile, width=width2, height=height, show=show)
    
    
    return rate_plot, pval_heat


In [41]:
def lowess_fit(single_data_df, timestep=5/60, window=24, plot=True):
    """
    Function to perform a LOWESS fit of PCA oxidation data.
    
    Params:
    -------
    single_data_df : pandas DataFrame
        The data for a single strain under a single condition from a single experiment.
        This is either a biological replicate from a single well or the mean of
        technical replicates from a given day.
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    window : int, default 24
        The number of time points oover which the LOWESS algorith should smooth.
        If the timestep is 5/60, a window of 24 corresponds to 2 hours
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    x = single_data_df['Time [hr]'].values
    y = single_data_df['measured PCAred (µM)'].values
    
    smoothed = sm.nonparametric.lowess(
        exog=x, 
        endog=y,
        is_sorted=False,
        return_sorted=True,
        frac=0.05
    )
    
    if plot:
        lowess_fit_plot = bokeh.plotting.figure(width=600, height=400)
        
        lowess_fit_plot.circle(x=x, y=y)
        lowess_fit_plot.line(smoothed[:,0], smoothed[:,1], line_width=2, color='red')
        
        bokeh.io.show(lowess_fit_plot)
    
    return smoothed[:,0], smoothed[:,1]
    

In [42]:
def get_lowess_derivative(lowess_x, lowess_y, timestep=5/60, plot=True):
    """
    Function to calculate the derivative of a LOWESS fit of PCA oxidation data.
    
    Params:
    -------
    lowess_x : numpy array
        The x-axis (time points) of the lowess fit
        
    lowess_y : numpy array
        The y-axis (PCAred concentration) of the lowess fit
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    derivative = np.gradient(lowess_y, timestep)
    
    if plot:
        lowess_derivative_plot = bokeh.plotting.figure(width=600, height=400)
        
        lowess_derivative_plot.line(lowess_x, derivative)
        
        bokeh.io.show(lowess_derivative_plot)
    
    return derivative

In [43]:
def get_max_oxidation_rate_from_lowess_fit(single_data_df, timestep=5/60, window=24, plot=True):
    """
    Function to perform a LOWESS fit of PCA oxidation data.
    
    Params:
    -------
    single_data_df : pandas DataFrame
        The data for a single strain under a single condition from a single experiment.
        This is either a biological replicate from a single well or the mean of
        technical replicates from a given day.
        
    timestep : float, default 5/60
        The interval (in hours) between measurements in the timeseries
        
    window : int, default 24
        The number of time points oover which the LOWESS algorith should smooth.
        If the timestep is 5/60, a window of 24 corresponds to 2 hours
        
    plot : Bool, default True
        Should this function plot the data and fit?
    """
    
    lowess_x, lowess_y = lowess_fit(single_data_df, timestep=timestep, window=window, plot=plot)
    derivative = get_lowess_derivative(lowess_x, lowess_y, timestep=timestep, plot=plot)
    
    max_oxidation_rate = np.max(derivative * -1)
    
    return max_oxidation_rate

In [44]:
def scan_lowess_frac(single_data_df, palette=bokeh.palettes.Viridis256[::-1]):
    
    """
    Function to scan across the "frac" parameter for the LOWESS fitting
    function to assess whether my choice of parameter is reasonable.
    
    This is for Supplementary Figure 4.1
    """
    
    from bokeh.models import LinearColorMapper, ColorBar
    
    times = single_data_df['Time [hr]'].values

    interval = np.mean([x2-x1 for x2, x1 in zip(times[1:], times[:-1])])
    
    fs = []
    tmaxs = []
    maxs = []
    
    i = 0
    
    smoothing_plot = bokeh.plotting.figure(
        width=400,
        height=300,
        x_axis_label = 'Time (hours)',
        y_axis_label = 'PCAred (µM)'
    )
    
    
    smoothing_plot.circle(
        x=single_data['Time [hr]'].values, 
        y=single_data['measured PCAred (µM)'].values, 
        size=20, color='white', 
        line_color='black',
        line_alpha=0.3,
        alpha=0.01
    )
    
    indicated_palette = [c for c in palette[::-1]]
    indicated_palette[13] ='red'

    color_mapper = LinearColorMapper(palette=indicated_palette, low=0, high=1)
    
    for f in np.arange(0, 1, 0.00391)[::-1]: # Give 256 steps
        
        smoothed = sm.nonparametric.lowess(
            exog=single_data['Time [hr]'].values, 
            endog=single_data['measured PCAred (µM)'].values,
            is_sorted=False,
            return_sorted=True,
            frac=f # The fraction of data used for smoothing window
        )
        
        derivative = np.gradient(smoothed[:,1], interval)
        
        max_rate_index = np.where(derivative == np.min(derivative))[0][0]
        time_of_max_rate = smoothed[:,0][max_rate_index]
        max_rate = np.max(derivative * -1)
        
        fs.append(f)
        tmaxs.append(time_of_max_rate)
        maxs.append(max_rate)
        # print(i)
        
        smoothing_plot.line(x=smoothed[:,0], y=smoothed[:,1], color=palette[i], line_width=2, alpha=0.1)
        
        i += 1
        
    color_bar = ColorBar(color_mapper=color_mapper, padding=5, title='LOWESS fraction')
    smoothing_plot.add_layout(color_bar, "right")
    # return fs, tmaxs, maxs
        
    max_rate_scan_plot = bokeh.plotting.figure(
        width=400,
        height=300,
        x_axis_label='LOWESS window (fraction of data)',
        y_axis_label='Max PCA oxidation rate (µM/hr)',
        y_range=(0,50)
    )
    
    max_rate_scan_plot.circle(fs, maxs, color=palette)
    # max_rate_scan_plot.line([0.05, 0.05], [0, np.max(maxs)], color='red')
    
    tmax_scan_plot = bokeh.plotting.figure(
        width=400,
        height=300,
        x_axis_label='LOWESS window (fraction of data)',
        y_axis_label='Time of max PCA oxidation rate (hours)',
        y_range=(0,4)
    )
    
    tmax_scan_plot.circle(fs, tmaxs, color=palette)
    # tmax_scan_plot.line([0.05, 0.05], [0, np.max(tmaxs)], color='red')
    
    two_d_plot = bokeh.plotting.figure(
        width=400,
        height=300,
        y_axis_label='Max oxidation rate (µM/hr)',
        x_axis_label='Time of max PCA oxidation rate (hours)'
    )
    
    two_d_plot.circle(tmaxs, maxs, color=palette)
    
    
    # Now, add on the fit that was used in paper
    selected_smooth = sm.nonparametric.lowess(
            exog=single_data['Time [hr]'].values, 
            endog=single_data['measured PCAred (µM)'].values,
            is_sorted=False,
            return_sorted=True,
            frac=0.05 # The fraction of data used for smoothing window
        )
    selected_derivative = np.gradient(selected_smooth[:,1], interval)
    selected_max_rate_index = np.where(selected_derivative == np.min(selected_derivative))[0][0]
    selected_time_of_max_rate = selected_smooth[:,0][selected_max_rate_index]
    
    smoothing_plot.line(x=selected_smooth[:,0], y=selected_smooth[:,1], color='red', line_width=1, alpha=0.7)
    max_rate_scan_plot.square(0.05, np.max(selected_derivative * -1), line_color='red', size=10, alpha=0, line_alpha=1, line_width=2)
    tmax_scan_plot.square(0.05, selected_time_of_max_rate, line_color='red', size=10, alpha=0, line_alpha=1, line_width=2)
    two_d_plot.square(selected_time_of_max_rate, np.max(selected_derivative * -1), line_color='red', size=10, alpha=0, line_alpha=1, line_width=2)
    
    
    
    smoothing_plot.output_backend = 'svg'
    max_rate_scan_plot.output_backend = 'svg'
    tmax_scan_plot.output_backend = 'svg'
    two_d_plot.output_backend = 'svg'
    
    return [smoothing_plot, two_d_plot, max_rate_scan_plot, tmax_scan_plot]
        
        

### See how my bootstrapping test compares to a t-test

In [45]:
rng = np.random.default_rng()

In [46]:
# You can fiddle with these parameters and run it a bunch of times to get a sense
a = scipy.stats.norm.rvs(loc=11, scale=5, size=200, random_state=rng)
b = scipy.stats.norm.rvs(loc=10, scale=5, size=200, random_state=rng)


In [47]:
scipy.stats.ttest_ind(a, b, equal_var=False)[1]

0.0031857128208864598

In [48]:
bootstrap_hypothesis_test_mean(a, b)

0.002966

In [49]:
bootstrap_efron_tibshirani(a, b, num_permutations=1000000)

0.002942

In [50]:
a2 = scipy.stats.norm.rvs(loc=20, scale=10, size=5, random_state=rng)

In [51]:
scipy.stats.ttest_ind(a2, b, equal_var=False, alternative='two-sided')[1]

0.10976276340841139

In [52]:
bootstrap_hypothesis_test_mean(a2, b)

0.015298

In [53]:
bootstrap_efron_tibshirani(a2, b, num_permutations=1000000)

0.015146

Overall, when the variances in the two samples are equal, the bootstrapped hypothesis test is more-or-less equivalent to the Student's t-test. When the variances are not equal, the test starts behaving differently (smaller p-values than for the Student's t-test). When the distributions that the samples are taking from are not Gaussian, the Student's t-test does not apply. With my data, there are no guarantees that the sample distributions are Gaussian or that the variances are equal.

Note: because the bootstrapping involves random re-sampling, every time you run the script, you will get slightly different p-values, but the qualitative meaning (i.e., statistical significance after Bonferroni correction) will remain unchanged.

#### Start plotting the meat and potatoes

In [55]:
nitrate_reductase_strain_regex = [
    r'Abiotic[0-9]*',
    r'WT[0-9]*',
    r'napA-tlKO[0-9]*',
    r'narG-tlKO[0-9]*',
    r'narZ-tlKO[0-9]*',
    r'napAnarZ-tlKO[0-9]*',
    r'narGnarZ-tlKO[0-9]*',
    r'narGnapA-tlKO[0-9]*',
    r'napAnarZnarG-tlKO[0-9]*',
]

In [56]:
nitrate_complementation_strain_regex = [
    # r'Abiotic[0-9]*',
    # r'WT[0-9]*',
    # r'napA-tlKO[0-9]*',
    # r'narG-tlKO[0-9]*',
    # r'narZ-tlKO[0-9]*',
    # r'napAnarZ-tlKO[0-9]*',
    # r'narGnarZ-tlKO[0-9]*',
    # r'narGnapA-tlKO[0-9]*',
    r'napAnarZnarG-tlKO[0-9]*',
    r'napAnarZnarG \S*',
]

In [57]:
# A little test plot
lad, test = process_to_lowess_plot(
    nitrate_reductase_strain_regex, 
    ['PCA, NO3'], 
    ['Standing'], 
    calibrated_data, 
    width=400, 
    outfile=None,
    return_param='rate',
    # y_axis_label='time to 50% [PCAred]',
    # thresh=0.5
)

100%|███████████████████████████████████████████████████████████████| 60/60 [00:00<00:00, 84.18it/s]


In [58]:
lad.loc[lad['strain'] == 'napAnarZnarG-tlKO']

return param        date                            cat fill color  \
14      1.307166  2022_07_13  (PCA, NO3, napAnarZnarG-tlKO)    #2ca02c   
15      1.332155  2022_07_13  (PCA, NO3, napAnarZnarG-tlKO)    #2ca02c   
16      2.791805  2022_07_13  (PCA, NO3, napAnarZnarG-tlKO)    #2ca02c   
32      1.446732  2022_09_27  (PCA, NO3, napAnarZnarG-tlKO)    #2ca02c   
40      0.842987  2022_09_29  (PCA, NO3, napAnarZnarG-tlKO)    #2ca02c   
48     -0.792862  2022_10_05  (PCA, NO3, napAnarZnarG-tlKO)    #2ca02c   

     shape             strain line color  
14  circle  napAnarZnarG-tlKO      black  
15  circle  napAnarZnarG-tlKO      black  
16  circle  napAnarZnarG-tlKO      black  
32  square  napAnarZnarG-tlKO      black  
40  square  napAnarZnarG-tlKO      black  
48  square  napAnarZnarG-tlKO      black

In [59]:
lad.loc[lad['strain'] == 'Abiotic'].dropna()

return param        date                  cat fill color   shape   strain  \
0       1.489208  2022_06_28  (PCA, NO3, Abiotic)    #1f77b4  square  Abiotic   
4       1.031206  2022_07_13  (PCA, NO3, Abiotic)    #1f77b4  square  Abiotic   
54      0.672342  2022_10_11  (PCA, NO3, Abiotic)    #1f77b4  square  Abiotic   
58      0.564167  2022_11_22  (PCA, NO3, Abiotic)    #1f77b4  square  Abiotic   
59      0.827176  2022_12_07  (PCA, NO3, Abiotic)    #1f77b4  square  Abiotic   

   line color  
0       black  
4       black  
54      black  
58      black  
59      black

In [60]:
lad.dropna()['strain'].unique()

array(['WT', 'Abiotic', 'napA-tlKO', 'narG-tlKO', 'narZ-tlKO',
       'napAnarZ-tlKO', 'narGnapA-tlKO', 'narGnarZ-tlKO',
       'napAnarZnarG-tlKO'], dtype=object)

In [61]:
strains = lad['strain'].unique()
    
pairs = []
for s1 in strains:
    for s2 in strains:
        if ((s2, s1) not in pairs) and (s1 != s2):
            pairs.append((s1, s2))


pval_df = get_pval_df(lad, func=bootstrap_efron_tibshirani)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:10<00:00,  3.28it/s]


In [62]:
# A little test data frame
pval_df

x                  y     p_val label       color  \
0              WT            Abiotic  0.000000    **     #009E73   
1              WT          napA-tlKO  0.264063         gainsboro   
2              WT          narG-tlKO  0.000000    **     #009E73   
3              WT          narZ-tlKO  0.810619         gainsboro   
4              WT      napAnarZ-tlKO  0.000000    **     #009E73   
5              WT      narGnapA-tlKO  0.000000    **     #009E73   
6              WT      narGnarZ-tlKO  0.000000    **     #009E73   
7              WT  napAnarZnarG-tlKO  0.000000    **     #009E73   
8         Abiotic          napA-tlKO  0.000000    **     #009E73   
9         Abiotic          narG-tlKO  0.000000    **     #009E73   
10        Abiotic          narZ-tlKO  0.000000    **     #009E73   
11        Abiotic      napAnarZ-tlKO  0.000000    **     #009E73   
12        Abiotic      narGnapA-tlKO  0.000000    **     #009E73   
13        Abiotic      narGnarZ-tlKO  0.000000    **     #009E73   
14        Abiotic  napAnarZnarG-tlKO  0.602250         gainsboro   
15      napA-tlKO          narG-tlKO  0.000001    **     #009E73   
16      napA-tlKO          narZ-tlKO  0.556714         gainsboro   
17      napA-tlKO      napAnarZ-tlKO  0.000005    **     #009E73   
18      napA-tlKO      narGnapA-tlKO  0.000000    **     #009E73   
19      napA-tlKO      narGnarZ-tlKO  0.000000    **     #009E73   
20      napA-tlKO  napAnarZnarG-tlKO  0.000000    **     #009E73   
21      narG-tlKO          narZ-tlKO  0.000012    **     #009E73   
22      narG-tlKO      napAnarZ-tlKO  0.148682         gainsboro   
23      narG-tlKO      narGnapA-tlKO  0.164178         gainsboro   
24      narG-tlKO      narGnarZ-tlKO  0.013212     *     #E69F00   
25      narG-tlKO  napAnarZnarG-tlKO  0.000000    **     #009E73   
26      narZ-tlKO      napAnarZ-tlKO  0.000210    **     #009E73   
27      narZ-tlKO      narGnapA-tlKO  0.000000    **     #009E73   
28      narZ-tlKO      narGnarZ-tlKO  0.000000    **     #009E73   
29      narZ-tlKO  napAnarZnarG-tlKO  0.000000    **     #009E73   
30  napAnarZ-tlKO      narGnapA-tlKO  0.000078    **     #009E73   
31  napAnarZ-tlKO      narGnarZ-tlKO  0.000001    **     #009E73   
32  napAnarZ-tlKO  napAnarZnarG-tlKO  0.000000    **     #009E73   
33  narGnapA-tlKO      narGnarZ-tlKO  0.119725         gainsboro   
34  narGnapA-tlKO  napAnarZnarG-tlKO  0.000000    **     #009E73   
35  narGnarZ-tlKO  napAnarZnarG-tlKO  0.000000    **     #009E73   

                  legend  
0         **p < 1.39e-03  
1               p ≥ 0.05  
2         **p < 1.39e-03  
3               p ≥ 0.05  
4         **p < 1.39e-03  
5         **p < 1.39e-03  
6         **p < 1.39e-03  
7         **p < 1.39e-03  
8         **p < 1.39e-03  
9         **p < 1.39e-03  
10        **p < 1.39e-03  
11        **p < 1.39e-03  
12        **p < 1.39e-03  
13        **p < 1.39e-03  
14              p ≥ 0.05  
15        **p < 1.39e-03  
16              p ≥ 0.05  
17        **p < 1.39e-03  
18        **p < 1.39e-03  
19        **p < 1.39e-03  
20        **p < 1.39e-03  
21        **p < 1.39e-03  
22              p ≥ 0.05  
23              p ≥ 0.05  
24  *1.39e-03 ≤ p < 0.05  
25        **p < 1.39e-03  
26        **p < 1.39e-03  
27        **p < 1.39e-03  
28        **p < 1.39e-03  
29        **p < 1.39e-03  
30        **p < 1.39e-03  
31        **p < 1.39e-03  
32        **p < 1.39e-03  
33              p ≥ 0.05  
34        **p < 1.39e-03  
35        **p < 1.39e-03

In [63]:
pval_df['p_val'].values

array([0.00000e+00, 2.64063e-01, 0.00000e+00, 8.10619e-01, 0.00000e+00,
       0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00,
       0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 6.02250e-01,
       1.00000e-06, 5.56714e-01, 5.00000e-06, 0.00000e+00, 0.00000e+00,
       0.00000e+00, 1.20000e-05, 1.48682e-01, 1.64178e-01, 1.32120e-02,
       0.00000e+00, 2.10000e-04, 0.00000e+00, 0.00000e+00, 0.00000e+00,
       7.80000e-05, 1.00000e-06, 0.00000e+00, 1.19725e-01, 0.00000e+00,
       0.00000e+00])

In [64]:
calibrated_data.loc[(calibrated_data['Strain'] == 'napAnarZnarG-tlKO') & 
                    (calibrated_data['Medium'] == 'Standing') & 
                    (calibrated_data['Condition'] == 'PCA, NO3')]

Time [hr]             Strain    Medium Condition Condition Conc. (µM)  \
12        0.068  napAnarZnarG-tlKO  Standing  PCA, NO3           222, 11111   
38        0.151  napAnarZnarG-tlKO  Standing  PCA, NO3           222, 11111   
64        0.234  napAnarZnarG-tlKO  Standing  PCA, NO3           222, 11111   
90        0.318  napAnarZnarG-tlKO  Standing  PCA, NO3           222, 11111   
116       0.401  napAnarZnarG-tlKO  Standing  PCA, NO3           222, 11111   
...         ...                ...       ...       ...                  ...   
7396     23.734  napAnarZnarG-tlKO  Standing  PCA, NO3           200, 10000   
7422     23.817  napAnarZnarG-tlKO  Standing  PCA, NO3           200, 10000   
7448     23.901  napAnarZnarG-tlKO  Standing  PCA, NO3           200, 10000   
7474     23.984  napAnarZnarG-tlKO  Standing  PCA, NO3           200, 10000   
7500     24.067  napAnarZnarG-tlKO  Standing  PCA, NO3           200, 10000   

     pregrowth condition        date  PCAred fluorescence (AU)  \
12            comparison  2022_09_27              40921.666667   
38            comparison  2022_09_27              41102.000000   
64            comparison  2022_09_27              41255.000000   
90            comparison  2022_09_27              41342.666667   
116           comparison  2022_09_27              41469.333333   
...                  ...         ...                       ...   
7396          comparison  2022_10_05              43477.333333   
7422          comparison  2022_10_05              43481.666667   
7448          comparison  2022_10_05              43477.333333   
7474          comparison  2022_10_05              43487.333333   
7500          comparison  2022_10_05              43594.000000   

      measured PCAred (µM)  
12              167.300786  
38              167.048730  
64              166.889103  
90              167.100202  
116             166.807853  
...                    ...  
7396            180.178124  
7422            180.361861  
7448            180.175930  
7474            180.646987  
7500            181.501959  

[866 rows x 9 columns]

In [65]:
# Plots for Figure 4D and F
rp, ph = bootstrapping(
    nitrate_reductase_strain_regex, 
    ['PCA, NO3'], 
    ['Standing'], 
    calibrated_data,
    func=bootstrap_efron_tibshirani,
    width1=400,
    width2=400,
    outfile='standing_nitrate',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_reductase_phenotypes_standing.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:10<00:00,  3.30it/s]


In [66]:
# Plots for Supplementary Figure 4.2B and D
rp, ph = bootstrapping(
    nitrate_reductase_strain_regex, 
    ['PCA, NO3'], 
    ['Standing'], 
    calibrated_data,
    func=bootstrap_efron_tibshirani,
    width1=400,
    width2=400,
    outfile='standing_nitrate_time',
    return_param='time',
    y_axis_label='Hours to 50% [PCAred]',
    thresh=0.5,
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_reductase_phenotypes_standing_times.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:06<00:00,  5.58it/s]


In [67]:
# Plots for Figure 4 C and E
rp, ph = bootstrapping(
    nitrate_reductase_strain_regex, 
    ['PCA, NO3'], 
    ['Shaking'], 
    calibrated_data,
    func=bootstrap_efron_tibshirani,
    width1=400,
    width2=400,
    outfile='shaking_nitrate',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_reductase_phenotypes_shaking.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:10<00:00,  3.37it/s]


In [68]:
# Plots for Supplementary Figure 4.2A and C.
rp, ph = bootstrapping(
    nitrate_reductase_strain_regex, 
    ['PCA, NO3'], 
    ['Shaking'], 
    calibrated_data,
    func=bootstrap_efron_tibshirani,
    width1=400,
    width2=400,
    outfile='shaking_nitrate_time',
    return_param='time',
    y_axis_label='Hours to 50% [PCAred]',
    thresh=0.5,
    show=False,
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_reductase_phenotypes_shaking_time.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:04<00:00,  8.09it/s]


In [69]:
# Plots for Supplementary Figure 4.3
rp, ph = bootstrapping(
    nitrate_complementation_strain_regex, 
    ['PCA, NO3'], 
    ['Standing'], 
    calibrated_data,
    func=bootstrap_efron_tibshirani,
    height=400,
    width1=300,
    width2=450,
    outfile='nitrate_complementation',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_reductase_complementation.svg')
bokeh.io.show(row)

100%|█████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.47it/s]


### Nitrate and quinones

In [70]:
nitrate_quinone_strain_regex = [
    r'Abiotic[0-9]*',
    r'WT[0-9]*',
    # r'napA-tlKO[0-9]*',
    # r'narG-tlKO[0-9]*',
    # r'narZ-tlKO[0-9]*',
    # r'napAnarZ-tlKO[0-9]*',
    # r'narGnarZ-tlKO[0-9]*',
    # r'narGnapA-tlKO[0-9]*',
    # r'napAnarZnarG-tlKO[0-9]*',
    r'menA-tlKO[0-9]*',
    r'ubiC-tlKO[0-9]*',
    r'menAubiC-tlKO[0-9]*',
    r'menAubiCnapAnarZ-tlKO[0-9]*',
    r'menAubiCnarGnapA-tlKO[0-9]*',
    r'menAubiCnarGnarZ-tlKO[0-9]*'
]

quinone_complementation_strain_regex = [
    r'Abiotic[0-9]*',
    r'menAubiC-tlKO[0-9]*',
    # r'menAubiCnapAnarZ-tlKO[0-9]*',
    # r'menAubiCnarGnapA-tlKO[0-9]*',
    # r'menAubiCnarGnarZ-tlKO[0-9]*',
    r'menAubiC \S*',
]

In [71]:
# Plots for Figure 5
rp, ph = bootstrapping(
    nitrate_quinone_strain_regex, 
    ['PCA, NO3'], 
    ['Standing'], 
    calibrated_data, 
    func=bootstrap_efron_tibshirani,
    width1=350,
    width2=450,
    outfile='nitrate_quinones',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_quinone_phenotypes.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 28/28 [00:08<00:00,  3.24it/s]


In [72]:
# Plots for Supplementary Figure 5.1
rp, ph = bootstrapping(
    quinone_complementation_strain_regex, 
    ['PCA, NO3'], 
    ['Standing'], 
    calibrated_data, 
    func=bootstrap_efron_tibshirani,
    width1=350,
    width2=450,
    outfile='nitrate_quinone_complementation',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/nitrate_quinone_complementations.svg')
bokeh.io.show(row)

100%|█████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.51it/s]


### DMSO and quinones

In [73]:
quinone_strain_regex = [
    r'Abiotic[0-9]*',
    r'WT[0-9]*',
    r'menA-tlKO[0-9]*',
    r'ubiC-tlKO[0-9]*',
    r'menAubiC-tlKO[0-9]*'
]

In [74]:
dmso_complementation_strain_regex1 = [
    r'Abiotic[0-9]*',
    r'WT[0-9]*',
    r'dmsA-tlKO[0-9]*',
    r'dmsA \S*',
    r'menA-tlKO[0-9]*',
    r'ubiC-tlKO[0-9]*',
    r'menAubiC-tlKO[0-9]*',
    r'menAubiC \S*'
]


In [75]:
# Plots for Figure 7 D and E.
rp, ph = bootstrapping(
    dmso_complementation_strain_regex1, 
    ['PCA, DMSO'], 
    ['Standing'], 
    calibrated_data, 
    func=bootstrap_efron_tibshirani,
    width1=400,
    width2=450,
    outfile='dmso_reductase_complementation',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/dmso_reductase_complementation.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:11<00:00,  3.04it/s]


#### Same for fumarate results

In [76]:
fum_complementation_strain_regex = [
    r'Abiotic[0-9]*',
    r'WT[0-9]*',
    r'frdA-tlKO[0-9]*',
    r'frdA \S*',
    r'menA-tlKO[0-9]*',
    r'ubiC-tlKO[0-9]*',
    r'menAubiC-tlKO[0-9]*',
    r'menAubiC \S*',
]


In [77]:
# Plots for Figure 7A and B
rp, ph = bootstrapping(
    fum_complementation_strain_regex, 
    ['PCA, Fum'], 
    ['Standing'], 
    calibrated_data, 
    func=bootstrap_efron_tibshirani,
    width1=400,
    width2=450,
    outfile='fumarate_complementation',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/fumarate_complementations.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 36/36 [00:09<00:00,  3.65it/s]


#### Now, for TMAO

In [78]:
# Plots for Figure 7G and H
tmao_complementation_strain_regex = [
    r'Abiotic[0-9]*',
    r'WT[0-9]*',
    r'dmsA-tlKO[0-9]*',
    r'dmsA \S*',
    r'dmsAtorA-tlKO[0-9]*',
    r'torA-tlKO[0-9]*'
]

tmao_calibrated_data = calibrated_data.loc[calibrated_data['date'].isin(
                                                 ['2022_10_06', '2022_10_07', '2022_11_22']
                                             )] # Using good batches of TMAO (no abiotic oxidation of PCA)

rp, ph = bootstrapping(
    tmao_complementation_strain_regex, 
    ['PCA, TMAO'], 
    ['Standing'], 
    tmao_calibrated_data,
    func=bootstrap_efron_tibshirani,
    width1=300,
    width2=400,
    outfile='tmao_complementation',
    return_param='rate',
    y_axis_label='Maximum PCAred oxidation rate (µM/hr)',
    show=False
)
row = bokeh.layouts.row([rp, ph])
bokeh.io.export_svg(row, filename=f'./plots/tmao_complementations.svg')
bokeh.io.show(row)

100%|███████████████████████████████████████████████████████████████| 15/15 [00:02<00:00,  5.02it/s]


### LOWESS analysis example:

In [79]:
single_data = calibrated_data.loc[(calibrated_data['Strain'].isin([
#                                                                     'Abiotic', 
#                                                                     'WT',
                                                                    'WT1',
#                                                                     'WT2',
#                                                                     'WT3',
#                                                                     'narG-tlKO',
                                                                    # 'napAnarZ-tlKO3'
#                                                                     'napAnarZnarG-tlKO', 
#                                                                     'frdA-tlKO', 
#                                                                     'dmsA-tlKO', 
#                                                                     'menA-tlKO', 
#                                                                     'menAubiC-tlKO',
#                                                                     'frdAB-tlKO3'
                                                                   ])) & 
                                   (calibrated_data['Condition'].isin([
#                                        'PCA', 
#                                        'PCA, Fum', 
                                       'PCA, NO3', 
#                                        'PCA, DMSO', 
#                                        'PCA, TMAO'
                                   ])) #&
# #                                    (calibrated_data['pregrowth condition'].isin(['standing'])) &
                                   & (calibrated_data['Medium'].isin(['Standing', 'Standing + POBM', 'Shaking'])) #&
# #                                    (calibrated_data['Well'] == 'E10') #&
                                   & (calibrated_data['date'].isin(['2022_07_13']))
                                  ].dropna()

In [80]:
times = single_data['Time [hr]'].values

interval = np.mean([x2-x1 for x2, x1 in zip(times[1:], times[:-1])])
interval * 60 # every timepoint was five minutes apart

4.9995652173913046

In [81]:
len(single_data['Time [hr]'].values) * interval

11.582326086956522

In [82]:
np.max(single_data['measured PCAred (µM)'].values)

183.32481261276504

In [83]:
single_plot = bokeh.plotting.figure(
    width=400, 
    height=300, 
    y_axis_label = 'PCAred (µM)', 
    x_axis_label='Time (hours)'
)

single_plot.circle(
    x=single_data['Time [hr]'].values, 
    y=single_data['measured PCAred (µM)'].values, 
    size=15, color='white', 
    line_color='black', 
    alpha=0.5
)

# half max
single_plot.line(
    x=[0, 12],
    y=[np.max(single_data['measured PCAred (µM)'].values)/2, np.max(single_data['measured PCAred (µM)'].values)/2],
    color='dodgerblue',
    line_width=1
)

# bokeh.io.show(single_plot)

smoothed = sm.nonparametric.lowess(
    exog=single_data['Time [hr]'].values, 
    endog=single_data['measured PCAred (µM)'].values,
    is_sorted=False,
    return_sorted=True,
    frac=0.05 # The fraction of data used for smoothing window
)

single_plot.line(x=smoothed[:,0], y=smoothed[:,1], color='red', line_width=2)
single_plot.output_backend = 'svg'
bokeh.io.show(single_plot)

In [84]:
derivative = np.gradient(smoothed[:,1], interval) # 5/60 is the time (in hours) between data points for these data

In [85]:
deriv_plot = bokeh.plotting.figure(
    width=400, 
    height=300,
    y_axis_label='Estimated PCA oxidation rate (µM/hr)',
    x_axis_label='Time (hours)'
)

max_rate_index = np.where(derivative == np.min(derivative))[0][0]
time_of_max_rate = smoothed[:,0][max_rate_index]


deriv_plot.line(x=smoothed[:,0], y=derivative * -1, line_width=2, color='red')

# time of max rate
deriv_plot.line(
    x=[time_of_max_rate, time_of_max_rate],
    y=[0, np.max(derivative * -1)],
    color='black',
    line_width=1
)
deriv_plot.output_backend = 'svg'
bokeh.io.show(deriv_plot)

In [86]:
np.min(derivative) * -1

38.41212670056437

In [87]:
np.where(derivative == np.min(derivative))[0][0]

28

In [88]:
smoothed[:,0][28]

2.401

In [89]:
# Plot for Figure 4A and B
bokeh.io.export_svg(bokeh.layouts.row([single_plot, deriv_plot]), filename='./plots/lowess_demo.svg')

['./plots/lowess_demo.svg']

In [90]:
bokeh.io.show(bokeh.layouts.gridplot(scan_lowess_frac(single_data), ncols=2))

In [91]:
# Supplementary Figure 4.1
bokeh.io.export_svg(bokeh.layouts.gridplot(scan_lowess_frac(single_data), ncols=2), filename='./plots/lowess_supplement.svg')

['./plots/lowess_supplement.svg']